# Group Lasso & Factor Analysis Model
Yuanchu Dang 

Oct. 26, 2016

## Roadmap
### (1) OnlineStats
### (2) Group Lasso
### (3) Factor Analysis Model
### (4) Implementation

## Brief intro to OnlineStats
- Everything is a type.
- e.g. $4$ different weights

In [1]:
using OnlineStats, Plots 
o1 = EqualWeight()
o2 = ExponentialWeight(.2)
o3 = BoundedEqualWeight(.2)
o4 = LearningRate(.5)
ovec = [o1, o2, o3, o4]
map(OnlineStats.updatecounter!, ovec)

plt_wt = plot([0], map(OnlineStats.weight, ovec)', w = 3,
label = ["EqualWeight" "ExponentialWeight(.2)" "BoundedEqualWeight(.2)" "LearningRate(.5)"],
xlabel = "nobs", ylabel = "weight value", layout = 4, ylims = (0, 1))
for i in 1:50
    for o in ovec
        OnlineStats.updatecounter!(o)
    end
    push!(plt_wt, nobs(o1), map(OnlineStats.weight, ovec))
end

In [2]:
@which OnlineStats.updatecounter!(o1)
@which OnlineStats.weight(o1)

weight(w::OnlineStats.EqualWeight) at C:\Users\think\.julia\v0.5\OnlineStats\src\weight.jl:113

In [3]:
plt_wt

- Another e.g. linear regression

In [5]:
using DataGenerator
x, y, β = linregdata(1_000, 5);
x2, y2, β2 = linregdata(1_000, 5);

# "standard" update
o = StatLearn(size(x, 2), SGD(), intercept = false)
plt_sgd1 = plot([0], [loss(o, x2, y2)], xlab = "nobs", ylab = "loss", ylims = (0, 2))
maprows(10, x, y) do xi, yi
    fit!(o, xi, yi); push!(plt_sgd1, nobs(o), [loss(o, x2, y2)])
end

# plot the loss history
plt_sgd1

## Lasso and Group Lasso

- OLS regression: $\min_{\beta} \frac{1}{2}||\mathbf{y} - X\beta||^2_2$
- Lasso: $\min_{\beta} \frac{1}{2}||\mathbf{y} - X\beta||^2_2 + \lambda ||\beta||_1$
- Group lasso: $\min_{\beta} \frac{1}{2}||\mathbf{y} - \sum_{l = 1}^m X^{(l)} \beta^{(l)}||^2_2 + \lambda \sum_{l = 1}^m \sqrt{p_l}||\beta^{(l)}||_2$



## Factor analysis model 

In many areas of psychology and behavioral sciences, it is often unfeasible to measure directly the concepts of primary interests. Instead, researchers only observe a set of "manifest variables" (denoted as $x$-variables) that are related to some latent factors of interest via linear relationships. The method of factor analysis is to uncover the hidden relationship between the observed $x$-variables and their latent factors.

Suppose we observe $p$ random variables, denoted as $\mathbf{X}=(X_1,\ldots,X_p)^T$, that are related to the latent factors via a relationship specified as follows:

$$
\boldsymbol{X} = \boldsymbol{\mu} + \boldsymbol{\Lambda} \boldsymbol{F} + \boldsymbol{\epsilon}
$$

where $\boldsymbol{X} = (X_1, ..., X_p)^T$ is assumed to follow a multivariate normal distribution with mean vector $\boldsymbol{\mu} = (\mu_1, ..., \mu_p)^T$ and variance-covariance matrix $\boldsymbol{\Sigma} = (\sigma_{ij})_{p\times p}$, $\boldsymbol{\Lambda} = (\lambda_{ij})_{p \times k}$ is a $p \times k$ matrix of factor loadings, and $\boldsymbol{F} = (F_1, ..., F_k)^T$ and $\boldsymbol{\epsilon} = (\epsilon_1, ..., \epsilon_p)^T$ are the latent factors and stochastic random errors respectively. In addition, it is conventional to assume that both $\boldsymbol{F}$ and $\epsilon$ are normally distributed, each with mean vector zero, and that $\boldsymbol{F}$ and $\boldsymbol{\epsilon}$ are independent from each other, that is, $E(\boldsymbol{F}\boldsymbol {\epsilon}^T) = \boldsymbol{0}$. Also, we assume that the variance-covariance matrices of $\boldsymbol{F}$ and $\epsilon$ are $E(\boldsymbol{F}\boldsymbol{F}^T)=\mathbf{I}_k, E(\boldsymbol{\epsilon} \boldsymbol{\epsilon}^T) = \boldsymbol{\Psi}$. Therefore, the variance-covariance matrix satisfies $\boldsymbol{\Sigma}=\boldsymbol{\Lambda} \boldsymbol{\Lambda^T}+\boldsymbol{\Psi}$.

## Variable selection
- Determine which x-variables are NOT explained by the hidden factors, i.e. $$\lambda_{i1} = \lambda_{i2} = ... = \lambda_{ik} = 0$$

## Solving the optimization

- Objective function

$$l_{\rho}^C = \sum_{n = 1}^N \log f(\mathbf{x_n}, \mathbf{f_n}) - N\rho P(\Lambda)$$

where $P(\Lambda) = \sum_{i = 1}^p ||\mathbf{\lambda_i}||_2$, and $\mathbf{\lambda_i}$ is the $i^{\text{th}}$ row of $\mathbf{\Lambda}$

- Factors are hidden variables, so need expectation-maximization (EM) algorithm.

- E-step
\begin{eqnarray*}
E[l_\rho^C(\theta)]&=&-\sum_{n=1}^N\{\frac{p+k}{2}\log(2\pi)+\frac{1}{2}\log |\Psi|+\frac{1}{2}tr[E(f_nf_n^T|x_n)]+\frac{1}{2}tr[\Psi^{-1}(x_n-\mu)(x_n-\mu)^T]\\
&-&tr[\Psi^{-1}(x_n-\mu)E(f_n)^T\Lambda^T]+\frac{1}{2}tr[\Psi^{-1}\Lambda E(f_nf_n^T|x_n)\Lambda^T]+\rho\sum_{i=1}^p \hat{\omega}_i||\lambda_i||\}
\end{eqnarray*}

- M-step

\begin{eqnarray*}
\hat{\Psi}=\frac{1}{n}\text{Diag}\left\lbrace \sum_{n=1}^N\left[(x_n-\mu)(x_n-\mu)^T-2(x_n-\mu)E(f_n|x_n)^T\hat{\Lambda}^T+\hat{\Lambda}E(f_nf_n^T|x_n)\hat{\Lambda}^T  \right]\right\rbrace.
\end{eqnarray*}

\begin{eqnarray*}
\hat{\lambda}_i=\left\lbrace\sum_{n=1}^N\left[ \frac{E(f_nf_n^T|x_n)}{\psi_i}+\left(\frac{\rho\hat{\omega}_i}{||\lambda_{i0}||}\right)\mathbb{I}_k \right] \right\rbrace^{-1}\left\lbrace\sum_{n=1}^N\frac{(x_{ni}-\bar{x}_i)E(f_n|x_n)}{\psi_i} \right\rbrace.
\end{eqnarray*}

- New type for factor model

In [6]:
type FactorModel
    p::Int # number of observable
    k::Int # number of factors
    lambda::Union{Array{Float64, 1}, Array{Float64, 2}} # loadings
    psi::Array{Float64, 2} # error covariance
end

- Code the EM algorithm for factor model by overwriting $fit!()$.

In [7]:
import StatsBase.fit!
function fit!(o::FactorModel, 
    x:: Array{Float64, 2}, 
    rho::Float64,
    run::Int, 
    thresh::Float64)
    
    # sample covariance
    s = cov(x)
    
    # get the field from o
    p = o.p
    k = o.k
    lambda = o.lambda
    psi = o.psi
    
    # loop run times
    for j in 1:run
        
        # update sigma and B
        sigma = lambda * lambda' + psi
        B = eye(k) - lambda' * inv(sigma) * lambda
        lambda_prev = lambda
        
        # update lambda
        for i in 1:p
            if sqrt(sum(lambda_prev[i,:].^2)) > thresh
                lambda[i,:] = inv((B + lambda_prev' * inv(sigma) * s * inv(sigma) * lambda_prev) / psi[i, i] + 
                rho * 1 / sqrt(sum(lambda_prev[i,:].^2)) * eye(k)) * (lambda_prev' * inv(sigma) * s[:, i] / psi[i, i])
            else
                lambda[i,:] = zeros(k)
            end
        end
        
        # update psi
        psi = diagm(diag(s - 2 * s * inv(sigma) * lambda_prev * lambda' + lambda * B * lambda' + 
        lambda * lambda_prev' * inv(sigma) * s * inv(sigma) * lambda_prev * lambda'))
    end
    o.lambda = lambda
    o.psi = psi
    o
end

fit! (generic function with 23 methods)

- Generate X-variables for $$\lambda = \begin{bmatrix}
    0.8 \\
    0.8 \\
    0.8 \\
    0 
    \end{bmatrix}$$
    $$\psi = diag(0.36, 0.36, 0.36, 1)$$.

In [8]:
using Distributions

# p := number of x-variable
p = 4 

# sample size
n = 50

# number of factors
k = 1

# real lambda
lambda_true = [0.8 0.8 0.8 0]'

# real psi
psi_true = 0.36 * eye(p)
psi_true[p, p] = 1

# real sigma
sigma_true = lambda_true * (lambda_true') + psi_true

# generate observation
m = MvNormal([0, 0, 0, 0], sigma_true)
x = rand(m, n)'

50×4 Array{Float64,2}:
  0.072812   -1.03643     0.0953876  -1.0184   
  0.54508    -0.54741    -0.700078   -0.0807212
  1.71816     0.168203   -0.374784   -0.247312 
  0.0986984  -1.05675    -0.657317   -1.95361  
 -0.0975305  -0.272238    1.03823     0.426233 
 -1.1726     -1.57272    -0.0211592  -0.486051 
 -0.553298   -0.275272    0.147574    0.858302 
 -0.0167533  -0.700604    0.315345   -1.69123  
 -1.55805    -0.908236   -0.999649   -0.886894 
  0.430138    0.498387    0.957923    0.163943 
 -1.31958    -0.40518    -1.58225     0.0230976
  0.916528    0.213175    2.00134    -0.86541  
  0.565216   -0.849429    1.3403      1.64688  
  ⋮                                            
  1.09635     0.829922    0.943013    0.800362 
  1.04157     0.319728    0.277024    3.44353  
  0.155828    1.22665     0.942084    0.359957 
 -1.08534    -0.0134574  -1.18327     1.71181  
 -0.433361   -0.544353   -1.44244    -0.526535 
  0.665031    0.604011   -0.187669   -0.47215  
 -0.722707   -1.2

In [9]:
lambda = [1 1 1 0.1]'; psi = eye(4) * 1.0
o = FactorModel(4, 1, lambda, psi)

FactorModel(4,1,[1.0; 1.0; 1.0; 0.1],[1.0 0.0 0.0 0.0; 0.0 1.0 0.0 0.0; 0.0 0.0 1.0 0.0; 0.0 0.0 0.0 1.0])

In [10]:
fit!(o, x, 0.05, 1000, 1e-10)

FactorModel(4,1,[0.494705; 0.474139; 0.482839; 0.0],[0.318122 0.0 0.0 0.0; 0.0 0.392062 0.0 0.0; 0.0 0.0 0.378319 0.0; 0.0 0.0 0.0 1.08706])

- Exploring a grid of different $\rho$'s

In [11]:
lambda = [1 1 1 0.1]'; psi = eye(4) * 1.0
o = FactorModel(4, 1, lambda, psi)
fit!(o, x, 0.0, 1000, 1e-10)
plt_rho = plot([0.0], o.lambda', xlab = "rho", ylab = "lambda", ylims = (-0.5, 1.5), 
label = ["Lambda 1" "Lambda 2" "Lambda 3" "Lambda 4"], layout = 4);

In [12]:
for rho in linspace(0.0, 1.0, 100)
    lambda = [1 1 1 0.1]'; psi = eye(4) * 1.0
    o = FactorModel(4, 1, lambda, psi)
    fit!(o, x, rho, 1000, 1e-10)
    push!(plt_rho, rho, o.lambda[:, 1])
end

In [13]:
plt_rho

- another example:

$$\Lambda = \begin{bmatrix}
    1 & 1 & 1 \\
    0 & 0 & 0 \\
    1 & 1 & 1 \\
    1 & 1 & 1 \\
    0 & 0 & 0
\end{bmatrix} $$

$$\psi = diag(0.1, 0.1, 0.1, 0.1, 0.1)$$

In [14]:
# new params
p2 = 5; n2 = 1000; k2 = 3
lambda_true2 = [1.0 1 1; 0 0 0; 1 1 1; 1 1 1; 0 0 0]
psi_true2 = eye(5) * 0.1
sigma_true2 = lambda_true2 * (lambda_true2') + psi_true2

# new sample
m2 = MvNormal([0.0, 0, 0, 0, 0], sigma_true2)
x2 = rand(m2, n2)'

# starting points
lambda2 = [1.3 0.9 1.0; 0.2 0.3 -0.2; 1.3 0.2 0.8; 1.0 1.0 1.0; -0.2 0.12 0.0]
psi2 = eye(5) * 0.12;

In [15]:
# run the EM
o2 = FactorModel(p2, k2, lambda2, psi2)
fit!(o2, x2, 0.5, 10000, 1e-10)

FactorModel(5,3,[0.83622 0.332831 0.587038; 0.0 0.0 0.0; … ; 0.846258 0.336826 0.594084; 0.0 0.0 0.0],[0.101462 0.0 … 0.0 0.0; 0.0 0.102309 … 0.0 0.0; … ; 0.0 0.0 … 0.0993661 0.0; 0.0 0.0 … 0.0 0.0937537])

In [16]:
o2.lambda

5×3 Array{Float64,2}:
 0.83622   0.332831  0.587038
 0.0       0.0       0.0     
 0.838992  0.333935  0.588984
 0.846258  0.336826  0.594084
 0.0       0.0       0.0     

In [17]:
o2.psi

5×5 Array{Float64,2}:
 0.101462  0.0       0.0       0.0        0.0      
 0.0       0.102309  0.0       0.0        0.0      
 0.0       0.0       0.114989  0.0        0.0      
 0.0       0.0       0.0       0.0993661  0.0      
 0.0       0.0       0.0       0.0        0.0937537

## Future work
- Adaptive weights for each row of $\Lambda$.
- Finer control with sparse group lasso (SGL)
$$\min_{\beta} \frac{1}{2}||\mathbf{y} - \sum_{l = 1}^m X^{(l)} \beta^{(l)}||^2_2 + (1 - \alpha) \lambda \sum_{l = 1}^m \sqrt{p_l}||\beta^{(l)}||_2 + \alpha \lambda ||\beta||_1$$
- Application to factor analysis model.
- Exploratory factor analysis (EFA) v.s. confirmatory factor analysis (CFA).